In [ ]:
%load_ext autoreload
%autoreload 2

# MLflow Regression Pipeline Notebook

This notebook runs the MLflow Regression Pipeline on Databricks and inspects its results. For more information about the MLflow Regression Pipeline, including usage examples, see the [Regression Pipeline overview documentation](https://mlflow.org/docs/latest/pipelines.html#regression-pipeline) the [Regression Pipeline API documentation](https://mlflow.org/docs/latest/python_api/mlflow.pipelines.html#module-mlflow.pipelines.regression.v1.pipeline).

## Setup

Initialize and inspect the pipeline. Configure MLflow logging.

In [1]:
from mlflow.pipelines import Pipeline

p = Pipeline()

2022/09/11 20:33:11 INFO mlflow.pipelines.pipeline: Creating MLflow Pipeline 'sklearn_regression'


In [2]:
p.inspect()

In [3]:
import os
import mlflow

mlflow.set_tracking_uri(f"sqlite:///{os.path.abspath('../metadata/mlflow/mlruns3.db')}")
mlflow.set_experiment(
    "sklearn_regression_experiment",
    artifact_location=os.path.abspath('../metadata/mlflow/mlartifacts')
)

<Experiment: artifact_location='/Users/corey.zumar/mlflow/examples/pipelines/sklearn_regression/metadata/mlflow/mlartifacts', experiment_id='1', lifecycle_stage='active', name='sklearn_regression_experiment', tags={}>

## Ingest

Ingest data for model development

In [6]:
ingested_df = p.ingest(
    location="./data/sample.parquet",
    format="parquet",
    use_cached=True,
)
target_col = "fare_amount"

## Split

Split data into train, validation, and test datasets

In [7]:
%%mlp_code steps/split.py

"""
This module defines the following routines used by the 'split' step of the regression pipeline:

- ``process_splits``: Defines customizable logic for processing & cleaning the training, validation,
  and test datasets produced by the data splitting procedure.
"""

from pandas import DataFrame

from mlflow.pipelines.decorators import mlp


@mlp
def process_splits(
    train_df: DataFrame, validation_df: DataFrame, test_df: DataFrame
) -> (DataFrame, DataFrame, DataFrame):
    """
    Perform additional processing on the split datasets.

    :param train_df: The training dataset produced by the data splitting procedure.
    :param validation_df: The validation dataset produced by the data splitting procedure.
    :param test_df: The test dataset produced by the data splitting procedure.
    :return: A tuple containing, in order: the processed training dataset, the processed
             validation dataset, and the processed test dataset.
    """

    def process(df: DataFrame):
        # Drop invalid data points
        cleaned = df.dropna()
        # Filter out invalid fare amounts and trip distance
        cleaned = cleaned[
            (cleaned["fare_amount"] > 0)
            & (cleaned["trip_distance"] < 400)
            & (cleaned["trip_distance"] > 0)
            & (cleaned["fare_amount"] < 1000)
        ]

        cleaned["pickup_dow"] = cleaned["tpep_pickup_datetime"].dt.dayofweek
        cleaned["pickup_hour"] = cleaned["tpep_pickup_datetime"].dt.hour
        trip_duration = (
            cleaned["tpep_dropoff_datetime"] - cleaned["tpep_pickup_datetime"]
        )
        cleaned["trip_duration"] = trip_duration.map(lambda x: x.total_seconds() / 60)

        return cleaned

    return process(train_df), process(validation_df), process(test_df)


In [8]:
train_df, val_df, test_df = p.split(
    split_ratios=[0.1, 0.1, 0.8],
    target_col=target_col,
    post_split_method=process_splits
)

2022/09/11 20:33:23 INFO mlflow.pipelines.steps.split: Creating hash buckets on input dataset containing 10000 rows consumes 0.06993412971496582 seconds.
2022/09/11 20:33:23 INFO mlflow.pipelines.steps.split: Running process_splits on train, validation and test datasets.


## Transform

Fit a transformer on the training dataset and apply the fitted transformer to the training and validation datasets

In [9]:
%%mlp_code steps/transform.py

"""
This module defines the following routines used by the 'transform' step of the regression pipeline:

- ``transformer_fn``: Defines customizable logic for transforming input data before it is passed
  to the estimator during model inference.
"""

from pandas import DataFrame
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline as SkPipeline
from sklearn.preprocessing import OneHotEncoder, StandardScaler, FunctionTransformer

from mlflow.pipelines.decorators import mlp

def calculate_features(df: DataFrame):
    """
    Extend the input dataframe with pickup day of week and hour, and trip duration.
    Drop the now-unneeded pickup datetime and dropoff datetime columns.
    """
    df["pickup_dow"] = df["tpep_pickup_datetime"].dt.dayofweek
    df["pickup_hour"] = df["tpep_pickup_datetime"].dt.hour
    trip_duration = (
            df["tpep_dropoff_datetime"] - df["tpep_pickup_datetime"]
    )
    df["trip_duration"] = trip_duration.map(lambda x: x.total_seconds() / 60)
    df.drop(columns=["tpep_pickup_datetime", "tpep_dropoff_datetime"], inplace=True)
    return df


@mlp
def transformer_fn():
    """
    Returns an *unfitted* transformer that defines ``fit()`` and ``transform()`` methods.
    The transformer's input and output signatures should be compatible with scikit-learn
    transformers.
    """
    return SkPipeline(
        steps=[
            (
                "calculate_time_and_duration_features",
                FunctionTransformer(calculate_features, feature_names_out="one-to-one"),
            ),
            (
                "encoder",
                ColumnTransformer(
                    transformers=[
                        (
                            "hour_encoder",
                            OneHotEncoder(categories="auto", sparse=False),
                            ["pickup_hour"],
                        ),
                        (
                            "day_encoder",
                            OneHotEncoder(categories="auto", sparse=False),
                            ["pickup_dow"],
                        ),
                        (
                            "std_scaler",
                            StandardScaler(),
                            ["trip_distance", "trip_duration"],
                        ),
                    ]
                ),
            ),
        ]
    )

In [10]:
transformed_train_df, transformed_val_df = p.transform(transformer_method=transformer_fn, target_col=target_col)

## Define metrics

Define metrics that will be used across the **Train** and **Evaluate** stages of the pipeline

In [11]:
%%mlp_code steps/metrics.py

"""
This module defines custom metric functions that are invoked during the 'train' and 'evaluate'
steps to provide model performance insights. Custom metric functions defined in this module are
referenced in the ``metrics`` section of ``pipeline.yaml``, for example:

.. code-block:: yaml
    :caption: Example custom metrics definition in ``pipeline.yaml``

    metrics:
      custom:
        - name: weighted_mean_squared_error
          function: weighted_mean_squared_error
          greater_is_better: False
"""

from typing import Dict

from pandas import DataFrame
from sklearn.metrics import mean_squared_error

from mlflow.pipelines.decorators import mlp


@mlp
def weighted_mean_squared_error(
    eval_df: DataFrame,
    builtin_metrics: Dict[str, int],  # pylint: disable=unused-argument
) -> Dict[str, int]:
    """
    Computes the weighted mean squared error (MSE) metric.

    :param eval_df: A Pandas DataFrame containing the following columns:

                    - ``"prediction"``: Predictions produced by submitting input data to the model.
                    - ``"target"``: Ground truth values corresponding to the input data.

    :param builtin_metrics: A dictionary containing the built-in metrics that are calculated
                            automatically during model evaluation. The keys are the names of the
                            metrics and the values are the scalar values of the metrics. For more
                            information, see
                            https://mlflow.org/docs/latest/python_api/mlflow.html#mlflow.evaluate.
    :return: A single-entry dictionary containing the MSE metric. The key is the metric name and
             the value is the scalar metric value. Note that custom metric functions can return
             dictionaries with multiple metric entries as well.
    """
    return {
        "weighted_mean_squared_error": mean_squared_error(
            eval_df["prediction"],
            eval_df["target"],
            sample_weight=1 / eval_df["prediction"].values,
        )
    }


In [12]:
metrics = {
    "custom": [
        {
            "name": "weighted_mean_squared_error",
            "function": weighted_mean_squared_error,  
            "greater_is_better": False
        },
    ],
    # Use the built-in "root_mean_squared_error" metric for ranking models during development
    "primary": "root_mean_squared_error",
}

## Train

Fit an estimator on the training data, save a pipeline model consisting of the fitted transformer and the fitted estimator, and evaluate the pipeline model on the training and validation datasets

In [13]:
%%mlp_code steps/train.py

"""
This module defines the following routines used by the 'train' step of the regression pipeline:

- ``estimator_fn``: Defines the customizable estimator type and parameters that are used
  during training to produce a model pipeline.
"""

from mlflow.pipelines.decorators import mlp


@mlp
def estimator_fn():
    """
    Returns an *unfitted* estimator that defines ``fit()`` and ``predict()`` methods.
    The estimator's input and output signatures should be compatible with scikit-learn
    estimators.
    """
    from sklearn.linear_model import SGDRegressor

    return SGDRegressor(random_state=42)

In [ ]:
model = p.train(estimator_method=estimator_fn, metrics=metrics, target_col=target_col)

## Evaluate

Evaluate the pipeline model on the test dataset and compare resulting performance metrics against specified validation criteria

In [ ]:
p.evaluate(
    metrics=metrics,
    validation_criteria=[
        {
            "metric": "root_mean_squared_error",
            "threshold": 100
        },
        {
            "metric": "mean_absolute_error",
            "threshold": 600
        },
        {
            "metric": "weighted_mean_squared_error",
            "threshold": 200
        },
    ],
    target_col=target_col,
)

## Register

Register the trained pipeline model with the MLflow Model Registry

In [ ]:
model_version = p.register(model_name="mymodel")